# Comparison results

This notebook will present the application of the TEDA-Ensemble algorithm to an electricity production dataset. A comparison will be made with LSTM, Linear Regressor, XGBoost, and kNN Regressor techniques.

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from matplotlib.lines import Line2D
import statsmodels.api as sm
import padasip as pa

from sklearn.metrics import mean_squared_error

import plotly.graph_objects as go
from plotly.subplots import make_subplots
import plotly.express as px

import datetime

import wandb
import logging

c:\Users\Samsung\anaconda3\lib\site-packages\pandas\core\computation\expressions.py:20: UserWarning: Pandas requires version '2.7.3' or newer of 'numexpr' (version '2.7.1' currently installed).
  from pandas.core.computation.check import NUMEXPR_INSTALLED


## Implemented modules and Padasip module

In [2]:
from padasip.filters.base_filter import AdaptiveFilter
from TedaEnsemble import DataCloud, TEDAEnsemble

from treating import dataTreating, dataSpliting, dataProcessing, dataSplit

## 2. Data loading:

In [3]:
df_results = pd.read_excel('results/results.xlsx')
df_results.head(7)

Model  RMSE_Minimum  RMSE_Mean  RMSE_Maximum  MAE_Minimum  \
0  TEDAEnsemble Stack      3.381888   8.422835     16.716014    11.437169   
1   TEDAEnsemble Pond      3.326150   7.741626     11.732573    11.063271   
2  TEDAEnsemble Major      3.369511   7.743462     11.581227    11.353607   
3   Linear Regression      4.761314   7.114945      8.036010     3.723006   
4                LSTM      2.249302   8.074360     10.254091     1.801173   
5                 XGB      3.960334  17.750109     41.977320     3.105552   

    MAE_Mean  MAE_Maximum  Energy_Minimum   Energy_Mean  Energy_Maximum  
0  77.760592   279.425111    0.000000e+00  3.360956e-08    1.923009e-07  
1  64.965445   137.653275    0.000000e+00  3.360956e-08    1.923009e-07  
2  64.963061   134.124812    0.000000e+00  3.360956e-08    1.923009e-07  
3   6.044648     6.927643    6.738327e-09  5.796341e-07    2.614804e-06  
4   7.020676     8.423756    1.223795e-06  1.462613e-06    3.489115e-06  
5  16.498920    41.013200    0.000000e+00  1.442148e-08    7.294103e-08

In [4]:
df_teda = pd.read_csv('results/TEDAEnsemble.csv')
df_lreg = pd.read_csv('results/LRegtoCompareWithTEDAEnsemble.csv')
df_lstm = pd.read_csv('results/LSTMtoCompareWithTEDAEnsemble.csv')
df_xgb = pd.read_csv('results/XGBtoCompareWithTEDAEnsemble.csv')
df_knn = pd.read_csv('results/KNNtoCompareWithTEDAEnsemble.csv')

### RMSE

In [5]:
df_teda_ = df_teda[['rmse_TEDA_pond', 'rmse_TEDA_stack', 'rmse_TEDA_major']].reset_index(drop=True)
df_lreg_ = df_lreg[['rmse_lreg']].reset_index(drop=True)
df_lstm_ = df_lstm[['rmse_lstm']].reset_index(drop=True)
df_xgb_ = df_xgb[['rmse_XGB']].reset_index(drop=True)
df_knn_ = df_knn[['rmse_KNN']].reset_index(drop=True)

df_aux = [df_teda_, df_lreg_, df_lstm_, df_xgb_, df_knn_]

df_rmse = pd.concat(df_aux, axis=1)

df_rmse.columns = ['Weighted', 'Stack', 'Major', 'LReg', 'LSTM', 'XGB', 'kNN']

df_rmse

Weighted     Stack     Major      LReg      LSTM        XGB       kNN
0    5.143705  9.550864  5.011179  4.761314  5.705199   7.549688  6.193248
1    3.766063  3.766063  3.766063  7.042670  7.214670   7.191103  5.976347
2    3.770247  4.659151  3.795357  7.707953  7.461478  40.827651  6.163397
3    3.869617  3.869617  3.869617  8.026775  7.687972   8.692210  6.053858
4    3.915816  3.785259  3.971238  8.036010  6.647504  40.827651  6.087496
..        ...       ...       ...       ...       ...        ...       ...
495  9.364110  9.364110  9.364110       NaN       NaN        NaN       NaN
496  9.191490  9.191490  9.191490       NaN       NaN        NaN       NaN
497  9.417752  9.417752  9.417752       NaN       NaN        NaN       NaN
498  8.884437  8.884437  8.884437       NaN       NaN        NaN       NaN
499  5.356252  5.356252  5.356252       NaN       NaN        NaN       NaN

[500 rows x 7 columns]

### MAE

In [6]:
df_teda_ = df_teda[['mae_TEDA_pond', 'mae_TEDA_stack', 'mae_TEDA_major']].reset_index(drop=True)
df_lreg_ = df_lreg[['mae_lreg']].reset_index(drop=True)
df_lstm_ = df_lstm[['mae_lstm']].reset_index(drop=True)
df_xgb_ = df_xgb[['mae_XGB']].reset_index(drop=True)
df_knn_ = df_knn[['mae_KNN']].reset_index(drop=True)

df_aux = [df_teda_, df_lreg_, df_lstm_, df_xgb_, df_knn_]

df_mae = pd.concat(df_aux, axis=1)

df_mae.columns = ['Weighted', 'Stack', 'Major', 'LReg', 'LSTM', 'XGB', 'kNN']

df_mae

Weighted      Stack      Major      LReg      LSTM        XGB       kNN
0    26.457705  91.219000  25.111914  3.723006  4.769030   5.721841  4.564043
1    14.183231  14.183231  14.183231  5.870982  5.829197   5.568732  4.545920
2    14.214761  21.707690  14.404733  6.801239  6.059737  40.001999  4.755398
3    14.973933  14.973933  14.973933  6.900370  6.467680   6.127859  4.630792
4    15.333612  14.328182  15.770730  6.927643  5.536965  40.001999  4.642069
..         ...        ...        ...       ...       ...        ...       ...
495  87.686558  87.686558  87.686558       NaN       NaN        NaN       NaN
496  84.483491  84.483491  84.483491       NaN       NaN        NaN       NaN
497  88.694054  88.694054  88.694054       NaN       NaN        NaN       NaN
498  78.933222  78.933222  78.933222       NaN       NaN        NaN       NaN
499  28.689432  28.689432  28.689432       NaN       NaN        NaN       NaN

[500 rows x 7 columns]

In [7]:
df_teda.head()

Name  Window  Factor  Threshold    Init  rmse_TEDA_pond  \
0      lemon-sweep-386       2    0.99        2.0    zero        5.143705   
1  visionary-sweep-141       2    0.75        2.3  Xavier        3.766063   
2   pleasant-sweep-131       2    0.75        1.8  Xavier        3.770247   
3      super-sweep-441       2    1.00        2.3  Xavier        3.869617   
4      giddy-sweep-156       2    0.75        1.8  Yoshua        3.915816   

   rmse_TEDA_stack  rmse_TEDA_major  mae_TEDA_pond  mae_TEDA_stack  \
0         9.550864         5.011179      26.457705       91.219000   
1         3.766063         3.766063      14.183231       14.183231   
2         4.659151         3.795357      14.214761       21.707690   
3         3.869617         3.869617      14.973933       14.973933   
4         3.785259         3.971238      15.333612       14.328182   

   mae_TEDA_major  Energy_Consumed  
0       25.111914     3.094961e-08  
1       14.183231     3.252950e-08  
2       14.404733     3.015506e-08  
3       14.973933     3.992518e-08  
4       15.770730     2.777038e-08

In [9]:
plt.figure(figsize=(15,7.7), dpi=1500)
plt.xticks(fontsize=15)
plt.yticks(fontsize=15)
plt.grid()

plt.xlabel("Window size", fontsize=20)
plt.ylabel("Root Mean Squared Error (RMSE) [epu]", fontsize=20)
plt.plot(df_rmse['Weighted'], 'b',  linewidth=3)
plt.legend(fontsize=15)

#plt.savefig('results_teda-ensemble_RMSE_x_window.png', format='png')

No artists with labels found to put in legend.  Note that artists whose label start with an underscore are ignored when legend() is called with no argument.


### Energy Consumed

In [10]:
df_teda_ = df_teda[['Energy_Consumed']].reset_index(drop=True)
df_lreg_ = df_lreg[['Energy_Consumed']].reset_index(drop=True)
df_lstm_ = df_lstm[['Energy_Consumed']].reset_index(drop=True)
df_xgb_ = df_xgb[['Energy_Consumed']].reset_index(drop=True)
df_knn_ = df_knn[['Energy_Consumed']].reset_index(drop=True)

df_aux = [df_teda_, df_lreg_, df_lstm_, df_xgb_, df_knn_]

df_energy = pd.concat(df_aux, axis=1)

df_energy.columns = ['TEDA-Ensemble', 'LReg', 'LSTM', 'XGB', 'kNN']

#df_energy.rename(columns={'Energy_Consumed': 'energy_teda', 'Energy_Consumed': 'energy_rls', 'Energy_Consumed': 'energy_lreg', 'Energy_Consumed': 'energy_lstm', 'Energy_Consumed': 'energy_xgb'})

In [11]:
# Tamanho do gráfico em polegadas
plt.figure(figsize = (15,7.7), dpi=1500)

# Cores dos boxplot
colors = ['#4435FB', '#3358FF', '#8A9EF9', '#FA605C', '#0FC885', '#F3D500', '#B446E8']

# plotviolin das espécies em relação ao tamanho das sépalas
ax = sns.boxplot(data = df_rmse, linewidth=1.5, palette=colors)
 

# Adicionando Título ao gráfico
plt.title("RMSE Boxplot", loc="center", fontsize=18)
plt.xlabel("Model", fontsize=15)
plt.ylabel("Root Mean Squared Error (RMSE) [epu]", fontsize=15)
plt.xticks(fontsize=12)
plt.yticks(fontsize=12)

#plt.show()
#plt.savefig('results_teda-ensemble_RMSE.eps', format='eps')

In [12]:
# Tamanho do gráfico em polegadas
plt.figure(figsize = (15,7.7), dpi=1500)

# Cores dos boxplot
colors = ['#4435FB', '#3358FF', '#8A9EF9', '#FA605C', '#0FC885', '#F3D500', '#B446E8']

# plotviolin das espécies em relação ao tamanho das sépalas
ax = sns.boxplot(data = df_mae, linewidth=1.5, palette=colors)
 

# Adicionando Título ao gráfico
plt.title("MAE Boxplot", loc="center", fontsize=18)
plt.xlabel("Model", fontsize=15)
plt.ylabel("Mean Absolute Error (MAE) [epu]", fontsize=15)
plt.xticks(fontsize=12)
plt.yticks(fontsize=12)

#plt.show()
#plt.savefig('results_teda-ensemble_MAE.eps', format='eps')

In [13]:
# Tamanho do gráfico em polegadas
plt.figure(figsize = (15,7.7), dpi=1500)

# Cores dos boxplot
colors = ['#4435FB', '#FA605C', '#0FC885', '#F3D500', '#B446E8']

# plotviolin das espécies em relação ao tamanho das sépalas
ax = sns.boxplot(data = df_energy, linewidth=1.5, palette=colors)
 

# Adicionando Título ao gráfico
plt.title("Energy Consumed Boxplot", loc="center", fontsize=18)
plt.xlabel("Model", fontsize=15)
plt.ylabel("Energy [W]", fontsize=15)
plt.xticks(fontsize=12)
plt.yticks(fontsize=12)

#plt.show()
#plt.savefig('results_teda-ensemble_energy.eps', format='eps')